In [ ]:
from dotenv import load_dotenv
from typing import Optional
import os
import yaml
import pandas as pd
import vectorbt as vbt
import numpy as np

load_dotenv()
config_path = os.getenv('3CANDLES_CONFIG_PATH')

with open(config_path, 'r') as file:
    config = yaml.safe_load(file)
    
df_hour = pd.read_csv(config['Data_filename'])
df_hour = df_hour.set_index('Time')
df_hour.index = pd.to_datetime(df_hour.index)

df_hour = df_hour.drop(columns=['Volume', 'High', 'Low'])
df_hour['Dir'] = 0

df_hour.loc[df_hour['Close'] > df_hour['Open'], 'Dir'] = 1
bull_entry_mask = ((df_hour['Dir'] == 1) & (df_hour['Dir'].shift(1) == 1) & (df_hour['Dir'].shift(2) == 1) & #short
                    (df_hour['Close'].shift(2) < df_hour['Open']))
df_hour['Bull Entry'] = bull_entry_mask
bear_entry_mask = ((df_hour['Dir'] == 0) & (df_hour['Dir'].shift(1) == 0) & (df_hour['Dir'].shift(2) == 0) & #long
                    (df_hour['Close'].shift(2) > df_hour['Open']))
df_hour['Bear Entry'] = bear_entry_mask

df_hour.loc[df_hour['Bull Entry'] == True, 'SL'] = df_hour['Close'] #short
df_hour.loc[df_hour['Bear Entry'] == True, 'SL'] = df_hour['Close'] #long

df_hour.loc[df_hour['Bull Entry'] == True, 'TP'] = df_hour['Close'] - ((df_hour['Close'] - df_hour['Close'].shift(2)) * config['RR']) #short
df_hour.loc[df_hour['Bear Entry'] == True, 'TP'] = df_hour['Close'] + ((df_hour['Close'].shift(2) - df_hour['Close']) * config['RR']) #long

index_arr_hour = df_hour.index.to_numpy()
open_arr_hour = df_hour['Open'].to_numpy()
close_arr_hour = df_hour['Close'].to_numpy()
bull_entry_arr_hour = df_hour['Bull Entry'].to_numpy()
bear_entry_arr_hour = df_hour['Bear Entry'].to_numpy()
sl_arr_hour = df_hour['SL'].to_numpy()
tp_arr_hour = df_hour['TP'].to_numpy()
price_arr_hour = np.full(len(index_arr_hour), np.nan)
bull_entrymask_arr_hour = np.full(len(index_arr_hour), False)
bear_entrymask_arr_hour = np.full(len(index_arr_hour), False)
bull_exit_arr_hour = np.full(len(index_arr_hour), False)
bear_exit_arr_hour = np.full(len(index_arr_hour), False)

trade_direct: Optional[str] = None
cur_sl: Optional[float] = None; cur_tp: Optional[float] = None

for i in range(len(index_arr_hour)):
    if trade_direct is None:

        if bull_entry_arr_hour[i]:
            trade_direct = 'bull'
            bull_entrymask_arr_hour[i] = True
            cur_sl, cur_tp = sl_arr_hour[i], tp_arr_hour[i]
            price_arr_hour[i] = close_arr_hour[i]
        elif bear_entry_arr_hour[i]:
            trade_direct = 'bear'
            bear_entrymask_arr_hour[i] = True
            cur_sl, cur_tp = sl_arr_hour[i], tp_arr_hour[i]
            price_arr_hour[i] = close_arr_hour[i]
        else:
            continue  

    elif trade_direct == 'bull':

        if close_arr_hour[i] >= cur_sl:
            price_arr_hour[i] = cur_sl
            trade_direct, cur_sl, cur_tp = None, None, None
            bull_exit_arr_hour[i] = True
        elif close_arr_hour[i] <= cur_tp:
            price_arr_hour[i] = cur_tp
            trade_direct, cur_sl, cur_tp = None, None, None
            bull_exit_arr_hour[i] = True

    elif trade_direct == 'bear':

        if close_arr_hour[i] <= cur_sl:
            price_arr_hour[i] = cur_sl
            trade_direct, cur_sl, cur_tp = None, None, None
            bear_exit_arr_hour[i] = True
        elif close_arr_hour[i] >= cur_tp:
            price_arr_hour[i] = cur_tp
            trade_direct, cur_sl, cur_tp = None, None, None
            bear_exit_arr_hour[i] = True

pf = vbt.Portfolio.from_signals(
entries = bear_entrymask_arr_hour,
exits = bear_exit_arr_hour,
short_entries = bull_entrymask_arr_hour,
short_exits = bull_exit_arr_hour,
price = price_arr_hour,
open = df_hour["Open"],
close = df_hour["Close"],
size = config['Trade']['size'],
size_type = config['Trade']['size_type'],
fees = config['Broker']['fees'],
fixed_fees = config['Broker']['fixed_fees'],
slippage = config['Slippage'],
init_cash = config['Initial_cash'],
freq = config['Frequency']
)

FileNotFoundError: [Errno 2] No such file or directory: 'config.yaml'

In [ ]:
pf.stats()

Start                         2024-01-01 22:00:00+00:00
End                           2025-12-02 21:00:00+00:00
Period                                499 days 00:00:00
Start Value                                     50000.0
End Value                                  53952.759771
Total Return [%]                                7.90552
Benchmark Return [%]                           5.229516
Max Gross Exposure [%]                        30.147084
Total Fees Paid                                  3223.0
Max Drawdown [%]                               0.219584
Max Drawdown Duration                  23 days 16:00:00
Total Trades                                       1612
Total Closed Trades                                1611
Total Open Trades                                     1
Open Trade PnL                                 1.784611
Win Rate [%]                                  28.119181
Best Trade [%]                                 1.215951
Worst Trade [%]                               -0

In [ ]:
pf.plot().show()

In [ ]:
pf.trades.records_readable.tail(21)

Exit Trade Id  Column          Size           Entry Timestamp  \
1591           1591       0  13969.104235 2025-11-26 02:00:00+00:00   
1592           1592       0  13979.810873 2025-11-26 08:00:00+00:00   
1593           1593       0  13957.703912 2025-11-26 16:00:00+00:00   
1594           1594       0  13953.574571 2025-11-26 18:00:00+00:00   
1595           1595       0  13951.973938 2025-11-26 20:00:00+00:00   
1596           1596       0  13941.956821 2025-11-27 00:00:00+00:00   
1597           1597       0  13942.518742 2025-11-27 04:00:00+00:00   
1598           1598       0  13956.199269 2025-11-28 04:00:00+00:00   
1599           1599       0  13978.114104 2025-11-28 08:00:00+00:00   
1600           1600       0  13991.138783 2025-11-28 10:00:00+00:00   
1601           1601       0  13937.176426 2025-11-28 15:00:00+00:00   
1602           1602       0  13918.912224 2025-12-01 09:00:00+00:00   
1603           1603       0  13911.692810 2025-12-01 11:00:00+00:00   
1604           1604       0  13909.139363 2025-12-01 15:00:00+00:00   
1605           1605       0  13918.557544 2025-12-01 17:00:00+00:00   
1606           1606       0  13932.668446 2025-12-01 19:00:00+00:00   
1607           1607       0  13935.392791 2025-12-02 00:00:00+00:00   
1608           1608       0  13928.914553 2025-12-02 03:00:00+00:00   
1609           1609       0  13935.595057 2025-12-02 10:00:00+00:00   
1610           1610       0  13950.016245 2025-12-02 16:00:00+00:00   
1611           1611       0  13923.053308 2025-12-02 20:00:00+00:00   

      Avg Entry Price  Entry Fees            Exit Timestamp  Avg Exit Price  \
1591          1.15818         1.0 2025-11-26 03:00:00+00:00         1.15818   
1592          1.15720         1.0 2025-11-26 09:00:00+00:00         1.15720   
1593          1.15904         1.0 2025-11-26 17:00:00+00:00         1.15904   
1594          1.15934         1.0 2025-11-26 19:00:00+00:00         1.15934   
1595          1.15943         1.0 2025-11-26 21:00:00+00:00         1.15943   
1596          1.16022         1.0 2025-11-27 01:00:00+00:00         1.16022   
1597          1.16008         1.0 2025-11-27 06:00:00+00:00         1.16008   
1598          1.15895         1.0 2025-11-28 05:00:00+00:00         1.15895   
1599          1.15704         1.0 2025-11-28 09:00:00+00:00         1.15704   
1600          1.15592         1.0 2025-11-28 13:00:00+00:00         1.15704   
1601          1.16074         1.0 2025-12-01 08:00:00+00:00         1.16074   
1602          1.16222         1.0 2025-12-01 10:00:00+00:00         1.16222   
1603          1.16278         1.0 2025-12-01 12:00:00+00:00         1.16278   
1604          1.16290         1.0 2025-12-01 16:00:00+00:00         1.16290   
1605          1.16207         1.0 2025-12-01 18:00:00+00:00         1.16207   
1606          1.16085         1.0 2025-12-01 23:00:00+00:00         1.16085   
1607          1.16058         1.0 2025-12-02 01:00:00+00:00         1.16089   
1608          1.16122         1.0 2025-12-02 04:00:00+00:00         1.16092   
1609          1.16066         1.0 2025-12-02 11:00:00+00:00         1.16107   
1610          1.15954         1.0 2025-12-02 19:00:00+00:00         1.16176   
1611          1.16246         1.0 2025-12-02 21:00:00+00:00         1.16226   

      Exit Fees        PnL    Return Direction  Status  Position Id  
1591        1.0  -2.000000 -0.000124     Short  Closed         1591  
1592        1.0  -2.000000 -0.000124      Long  Closed         1592  
1593        1.0  -2.000000 -0.000124     Short  Closed         1593  
1594        1.0  -2.000000 -0.000124     Short  Closed         1594  
1595        1.0  -2.000000 -0.000124     Short  Closed         1595  
1596        1.0  -2.000000 -0.000124     Short  Closed         1596  
1597        1.0  -2.000000 -0.000124      Long  Closed         1597  
1598        1.0  -2.000000 -0.000124     Short  Closed         1598  
1599        1.0  -2.000000 -0.000124      Long  Closed         1599  
1600